## The conversation of the stock prices to neutralize to USD

In [5]:
import pandas as pd

def convert_to_usd(stock_file, forex_file, metadata_file, output_file):
    """
    Converts stock prices in various currencies to USD using forex rates.

    Parameters:
    - stock_file (str): Path to the stock timeseries file.
    - forex_file (str): Path to the forex rates file.
    - metadata_file (str): Path to the stock metadata file.
    - output_file (str): Path where the converted CSV will be saved.
    """
    # Load datasets
    stock_data = pd.read_csv(stock_file)
    forex_data = pd.read_csv(forex_file)
    metadata = pd.read_csv(metadata_file)

    # Remove time part from forex data's Date column
    forex_data['Date'] = pd.to_datetime(forex_data['Date'].str[:10], errors='coerce')

    # Ensure dates in stock data are in correct format
    stock_data['Date'] = pd.to_datetime(stock_data['Date'], errors='coerce')

    # Ensure dates in forex data are also date-only (drop any time information)
    forex_data['Date'] = forex_data['Date'].dt.date
    stock_data['Date'] = stock_data['Date'].dt.date

    # Merge stock data with metadata to include currency information
    stock_data = stock_data.merge(metadata[['Symbol', 'Currency']], on='Symbol', how='left')

    # Initialize a list to store converted data
    converted_data = []

    # Iterate through the stock data
    for index, row in stock_data.iterrows():
        symbol = row['Symbol']
        date = row['Date']
        currency = row['Currency']

        # Copy USD values directly without conversion
        if currency == 'USD':
            for col in ['Adj Close', 'Close', 'High', 'Low', 'Open']:
                row[f'{col} USD'] = row[col]
            converted_data.append(row)
            continue

        # Find the forex rate for the specific date and currency
        forex_column = f"{currency}USD=X"
        if forex_column not in forex_data.columns:
            print(f"Warning: No forex column found for currency {currency}. Skipping symbol {symbol} on {date}.")
            continue

        # Get the forex rate for the specific date or find the most recent available rate
        forex_rate_row = forex_data[forex_data['Date'] == date]

        if forex_rate_row.empty:
            forex_rate_row = forex_data[forex_data['Date'] < date].sort_values(by='Date', ascending=False).head(1)

        if forex_rate_row.empty:
            print(f"Warning: No forex rate available for currency {currency} on or before {date}. Using default rate of 1.0.")
            forex_rate = 1.0  # Default rate for missing data
        else:
            try:
                forex_rate = forex_rate_row[forex_column].values[0]
            except IndexError:
                print(f"Error: Unable to retrieve forex rate for {currency} on {date}. Using default rate of 1.0.")
                forex_rate = 1.0

        # Log the forex rate used
        print(f"Using forex rate {forex_rate} for {currency} on {date}.")

        # Convert prices to USD
        for col in ['Adj Close', 'Close', 'High', 'Low', 'Open']:
            if pd.notna(row[col]):
                row[f'{col} USD'] = row[col] * forex_rate
            else:
                row[f'{col} USD'] = None

        converted_data.append(row)

    # Create a DataFrame from the converted data
    converted_df = pd.DataFrame(converted_data)

    # Select and save the necessary columns
    output_columns = ['Symbol', 'Date', 'Currency'] + [f'{col} USD' for col in ['Adj Close', 'Close', 'High', 'Low', 'Open']]
    converted_df = converted_df[output_columns]

    converted_df.to_csv(output_file, index=False)
    print(f"USD-converted data has been saved to {output_file}.")

# Paths to the datasets
stock_file = "/Users/erolberkiyibozkurt/Documents/GitHub/Python/Projects/The Influence of AI Boom on Tech Stocks/Extracted Data/stock_timeseries_different_currency.csv"
forex_file = "/Users/erolberkiyibozkurt/Documents/GitHub/Python/Projects/The Influence of AI Boom on Tech Stocks/Background Data/forex_rates.csv"
metadata_file = "/Users/erolberkiyibozkurt/Documents/GitHub/Python/Projects/The Influence of AI Boom on Tech Stocks/Extracted Data/stock_metadata_top100.csv"
output_file = "/Users/erolberkiyibozkurt/Documents/GitHub/Python/Projects/The Influence of AI Boom on Tech Stocks/Extracted Data/stock_timeseries_usd_full.csv"

convert_to_usd(stock_file, forex_file, metadata_file, output_file)


Using forex rate 0.0008830801816657 for KRW on 2010-01-04.
Using forex rate 0.0008830801816657 for KRW on 2010-01-04.
Using forex rate 0.1289374232292175 for HKD on 2010-01-04.
Using forex rate 0.0313873179256916 for TWD on 2010-01-04.
Using forex rate 0.0313873179256916 for TWD on 2010-01-04.
Using forex rate 0.0313873179256916 for TWD on 2010-01-04.
Using forex rate 0.0108113950118422 for JPY on 2010-01-04.
Using forex rate 0.0108113950118422 for JPY on 2010-01-04.
Using forex rate 0.0108113950118422 for JPY on 2010-01-04.
Using forex rate 0.0108113950118422 for JPY on 2010-01-04.
Using forex rate 0.960614800453186 for CAD on 2010-01-04.
Using forex rate 0.0306880269199609 for THB on 2010-01-04.
Using forex rate 1.4423978328704834 for EUR on 2010-01-04.
Using forex rate 1.4423978328704834 for EUR on 2010-01-04.
Using forex rate 1.4423978328704834 for EUR on 2010-01-04.
Using forex rate 1.4423978328704834 for EUR on 2010-01-04.
Using forex rate 0.0008761937497183 for KRW on 2010-01-05